## Fine-tune large models using 🤗 [`peft`](https://github.com/huggingface/peft) adapters, [`transformers`](https://github.com/huggingface/transformers) & [`bitsandbytes`](https://github.com/TimDettmers/bitsandbytes)

In this tutorial we will cover how we can fine-tune large language models using the very recent `peft` library and `bitsandbytes` for loading large models in **4-bit**.
The fine-tuning method will rely on a recent method called "Low Rank Adapters" (LoRA), instead of fine-tuning the entire model you just have to fine-tune these adapters and load them properly inside the model. We will be using the 4-bit implementation first described in the [QLoRA](https://arxiv.org/abs/2305.14314) paper. 
After fine-tuning the model you can also share your adapters on the 🤗 Hub and load them very easily. Let's get started!

### Install requirements

First, run the cells below to install the requirements:

In [1]:
!pip install -q -U bitsandbytes datasets loralib einops
!pip install -q -U git+https://github.com/huggingface/transformers.git 
!pip install -q -U git+https://github.com/huggingface/peft.git
!pip install -q -U git+https://github.com/huggingface/accelerate.git
!pip install -q datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.2/92.2 MB 17.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.6/474.6 kB 35.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 4.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 10.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 13.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 38.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 19.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.5/114.5 kB 5.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 1.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.6/149.6 kB 13.6 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (py

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
from huggingface_hub import notebook_login

notebook_login()

In [4]:
!nvidia-smi

Tue May 30 04:38:26 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100-SXM...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   35C    P0    47W / 400W |      0MiB / 40960MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

import torch
import torch.nn as nn
import bitsandbytes as bnb
from transformers import AutoTokenizer, AutoConfig, AutoModelForCausalLM, BitsAndBytesConfig

In [6]:
free_in_GB = int(torch.cuda.mem_get_info()[0] / 1024**3)
max_memory = f"{free_in_GB-2}GB"

n_gpus = torch.cuda.device_count()
max_memory = {i: max_memory for i in range(n_gpus)}
max_memory

{0: '37GB'}

### Model loading

In [7]:
model_id = "tiiuae/falcon-40b"

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

model = AutoModelForCausalLM.from_pretrained(
    model_id,
    quantization_config=bnb_config,
    device_map={"":0},
    trust_remote_code=True,
)

tokenizer = AutoTokenizer.from_pretrained(model_id)

A new version of the following files was downloaded from https://huggingface.co./tiiuae/falcon-40b:
- configuration_RW.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


A new version of the following files was downloaded from https://huggingface.co./tiiuae/falcon-40b:
- modelling_RW.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


Loading checkpoint shards:   0%|          | 0/9 [00:00<?, ?it/s]

### Prepare model for training

Some pre-processing needs to be done before training such an int8 model using `peft`, therefore let's import an utiliy function `prepare_model_for_kbit_training` that will: 
- Casts all the non `nf4` modules to full precision (`fp32`) for stability
- Add a `forward_hook` to the input embedding layer to enable gradient computation of the input hidden states
- Enable gradient checkpointing for more memory-efficient training

In [8]:
from peft import prepare_model_for_kbit_training

model.gradient_checkpointing_enable()
model = prepare_model_for_kbit_training(model)

### Apply LoRA

Here comes the magic with `peft`! Let's load a `PeftModel` and specify that we are going to use low-rank adapters (LoRA) using `get_peft_model` utility function from `peft`.

In [9]:
def print_trainable_parameters(model):
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )

In [10]:
from peft import LoraConfig, get_peft_model

config = LoraConfig(
    r=8, 
    lora_alpha=32, 
    target_modules=["query_key_value"], 
    lora_dropout=0.05, 
    bias="none", 
    task_type="CAUSAL_LM"
)

model = get_peft_model(model, config)
print_trainable_parameters(model)

trainable params: 8355840 || all params: 20927332352 || trainable%: 0.03992787928940901


In [11]:
# Verifying the datatypes.
dtypes = {}
for _, p in model.named_parameters():
    dtype = p.dtype
    if dtype not in dtypes:
        dtypes[dtype] = 0
    dtypes[dtype] += p.numel()
total = 0
for k, v in dtypes.items():
    total += v
for k, v in dtypes.items():
    print(k, v, v / total)

torch.float32 543014912 0.02594764124095849
torch.uint8 20384317440 0.9740523587590415


### Training

In [12]:
import transformers
from datasets import load_dataset, Dataset
import pandas as pd
import numpy as np

In [13]:
# extract, load, and transform OpenAssistant/oasst1 chatbot dataset

# set some pandas options to make the output more readable
pd.set_option("display.max_rows", 500)
pd.set_option("display.max_columns", 500)
pd.set_option("display.width", 1000)

In [14]:
# load dataset from huggingface datasets
ds = load_dataset("OpenAssistant/oasst1")
# lets convert the train dataset to a pandas df
df = ds["train"].to_pandas()

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/84437 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/4401 [00:00<?, ? examples/s]

Dataset parquet downloaded and prepared to /root/.cache/huggingface/datasets/OpenAssistant___parquet/OpenAssistant--oasst1-2960c57d7e52ab15/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [15]:
# lets grab the message trees to train on 
message_tree_ids = np.unique(np.array(df["message_tree_id"]))
messages = {}
messages['message_tree_id'] = []
messages['message_tree_text'] = []

for message_tree_id in message_tree_ids:
    try:
        # look at all data for this message tree
        one_message_tree = df.query(f"message_tree_id == '{message_tree_id}'").sort_values("created_date")
        text = ""
    
        # root message
        text += "<human>: " + one_message_tree.iloc[0].text
        # find root message's children
        children = one_message_tree[one_message_tree.parent_id == one_message_tree.iloc[0].message_id]
        # find root message's top ranked child:
        child = children[children['rank'] == 0.0]
        text += '\n' + "<bot>: " + child.iloc[0].text
    
        # proceed through rest of the above message tree until completion
        flag=True
        while flag:
            try:
                # find next prompt
                children = one_message_tree[one_message_tree.parent_id == child.message_id.iloc[0]]
                children.index
                one_message_tree.loc[children.index].iloc[0].role
                text += '\n' + "<human>: " + one_message_tree.loc[children.index].iloc[0].text
    
                # find next children
                children = one_message_tree[one_message_tree.parent_id == one_message_tree.loc[children.index].iloc[0].message_id]
                children
                # find top ranked child:
                child = children[children['rank'] == 0.0]
                text += '\n' + "<bot>: " + child.iloc[0].text
            except:
                flag=False
    
        messages['message_tree_id'].append(message_tree_id)
        messages['message_tree_text'].append(text)

    except IndexError:
        pass

message_df = pd.DataFrame.from_dict(messages)


In [16]:
# check some random messages

i=41
print(message_df.message_tree_text.iloc[i])
print('\n')
print(message_df.iloc[i])

<human>: What is the capital of Japan?
<bot>: Tokyo is the capital of Japan.
<human>: And what is the capital of the Moon?
<bot>: Since the Moon is not currently inhabited by humans, there is currently no capital of the Moon.


message_tree_id                   01505c0f-2d68-4206-acfc-7ab39033c75a
message_tree_text    <human>: What is the capital of Japan?\n<bot>:...
Name: 41, dtype: object


In [19]:
# convert back to HF datasets format

data = Dataset.from_pandas(message_df)
data

Dataset({
    features: ['message_tree_id', 'message_tree_text'],
    num_rows: 9823
})

In [20]:
tokenizer.pad_token = tokenizer.eos_token

data = data.map(lambda samples: tokenizer(samples["message_tree_text"], padding=True, truncation=True,), batched=True)
data

Map:   0%|          | 0/9823 [00:00<?, ? examples/s]

Dataset({
    features: ['message_tree_id', 'message_tree_text', 'input_ids', 'token_type_ids', 'attention_mask'],
    num_rows: 9823
})

In [21]:
training_args = transformers.TrainingArguments(
    auto_find_batch_size=True,
    gradient_accumulation_steps=4,
    num_train_epochs=1,
    learning_rate=2e-5,
    fp16=True,
    save_total_limit=4,
    logging_steps=25,
    output_dir="/content/drive/MyDrive/Colab Files/WM/falcon-chat-40b",
    save_strategy='epoch',
    optim="paged_adamw_8bit",
    lr_scheduler_type = 'cosine',
    warmup_ratio = 0.05,
)

trainer = transformers.Trainer(
    model=model,
    train_dataset=data,
    args=training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)
model.config.use_cache = False  # silence the warnings. Please re-enable for inference!
trainer.train()

You're using a PreTrainedTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 23>:23                                                                            │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/trainer.py:1696 in train                    │
│                                                                                                  │
│   1693 │   │   inner_training_loop = find_executable_batch_size(                                 │
│   1694 │   │   │   self._inner_training_loop, self._train_batch_size, args.auto_find_batch_size  │
│   1695 │   │   )                                                                                 │
│ ❱ 1696 │   │   return inner_training_loop(                                                       │
│   1697 │   │   │   args=args,                                                                    │
│   1698 │   │   │   resume_from_checkpoint=resume_from_checkpoint,                                │
│   1699 │   │   │   trial=trial,                                                                  │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/accelerate/utils/memory.py:132 in decorator              │
│                                                                                                  │
│   129 │   │   │   if batch_size == 0:                                                            │
│   130 │   │   │   │   raise RuntimeError("No executable batch size found, reached zero.")        │
│   131 │   │   │   try:                                                                           │
│ ❱ 132 │   │   │   │   return function(batch_size, *args, **kwargs)                               │
│   133 │   │   │   except Exception as e:                                                         │
│   134 │   │   │   │   if should_reduce_batch_size(e):                                            │
│   135 │   │   │   │   │   gc.collect()                                                           │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/trainer.py:2052 in _inner_training_loop     │
│                                                                                                  │
│   2049 │   │   │   │   │   self.state.epoch = epoch + (step + 1 + steps_skipped) / steps_in_epo  │
│   2050 │   │   │   │   │   self.control = self.callback_handler.on_step_end(args, self.state, s  │
│   2051 │   │   │   │   │                                                                         │
│ ❱ 2052 │   │   │   │   │   self._maybe_log_save_evaluate(tr_loss, model, trial, epoch, ignore_k  │
│   2053 │   │   │   │   else:                                                                     │
│   2054 │   │   │   │   │   self.control = self.callback_handler.on_substep_end(args, self.state  │
│   2055                                                                                           │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/trainer.py:2338 in _maybe_log_save_evaluate │
│                                                                                                  │
│   2335 │   │   │   self._globalstep_last_logged = self.state.global_step                         │
│   2336 │   │   │   self.store_flos()                                                             │
│   2337 │   │   │                                                                                 │
│ ❱ 2338 │   │   │   self.log(logs)                                                                │
│   2339 │   │                                               

## Share adapters on the 🤗 Hub

In [22]:
model.push_to_hub("dfurman/falcon-40b-chat-oasst1", use_auth_token=True)

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

adapter_model.bin:   0%|          | 0.00/33.5M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co./dfurman/falcon-40b-chat-oasst1/commit/ac771b1cd698d5d2c7ce270eb15924cd2ea366aa', commit_message='Upload model', commit_description='', oid='ac771b1cd698d5d2c7ce270eb15924cd2ea366aa', pr_url=None, pr_revision=None, pr_num=None)

## Load adapters from the Hub

You can also directly load adapters from the Hub using the commands below:

In [ ]:
import torch
from peft import PeftModel, PeftConfig
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig

peft_model_id = "dfurman/falcon-40b-chat-oasst1"
config = PeftConfig.from_pretrained(peft_model_id)

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

model = AutoModelForCausalLM.from_pretrained(
    config.base_model_name_or_path,
    quantization_config=bnb_config,
    device_map={"":0},
    trust_remote_code=True,
)
tokenizer = AutoTokenizer.from_pretrained(config.base_model_name_or_path)
tokenizer.pad_token = tokenizer.eos_token

# Load the Lora model
model = PeftModel.from_pretrained(model, peft_model_id)

## Inference

You can then directly use the trained model or the model that you have loaded from the 🤗 Hub for inference as you would do it usually in `transformers`.

In [3]:
prompt = """<human>: My name is Daniel. Write a short email to my closest friends inviting them to come to my home on Friday for a dinner party, I will make the food but tell them to BYOB. 
<bot>:"""

prompt

'<human>: My name is Daniel. Write a short email to my closest friends inviting them to come to my home on Friday for a dinner party, I will make the food but tell them to BYOB. \n<bot>:'

In [4]:
batch = tokenizer(
    prompt,
    padding=True,
    truncation=True,
    return_tensors='pt'
)
batch = batch.to('cuda:0')
batch

{'input_ids': tensor([[   39, 15564, 48190,  1814,  1536,   304,  8156,    25, 14687,   241,
          1866,  2572,   271,   491, 14710,  2153, 19549,   612,   271,  1239,
           271,   491,  1081,   313,  4201,   312,   241,  5947,  3054,    23,
           295,   451,   717,   248,  1655,   480,  1705,   612,   271, 15528,
         18791,    25,  4610,    39, 13359, 48190]], device='cuda:0'), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]],
       device='cuda:0'), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]],
       device='cuda:0')}

In [5]:
with torch.cuda.amp.autocast():
    output_tokens = model.generate(
        input_ids = batch.input_ids, 
        max_new_tokens=200,
        temperature=0.7,
        top_p=0.7,
        num_return_sequences=1,
        pad_token_id=tokenizer.eos_token_id,
        eos_token_id=tokenizer.eos_token_id,
    )

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1255: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co./docs/transformers/main_classes/text_generation)
  warnings.warn(


In [6]:
generated_text = tokenizer.decode(output_tokens[0], skip_special_tokens=True)
# Inspect message response in the outputs
print(generated_text.split("<human>: ")[1].split("<bot>: ")[-1])

Dear Friends,

I'm excited to invite you to a dinner party at my home on Friday, [date]. I will be making the food, but please bring your own beverages. I'm looking forward to seeing you and catching up!

Sincerely,
Daniel



In [7]:
prompt = """<human>: Create a list of four things to do in San Francisco. 
<bot>:"""

prompt

'<human>: Create a list of four things to do in San Francisco. \n<bot>:'

In [8]:
batch = tokenizer(
    prompt,
    padding=True,
    truncation=True,
    return_tensors='pt'
)
batch = batch.to('cuda:0')
batch

{'input_ids': tensor([[   39, 15564, 48190,  8715,   241,  1175,   275,  1855,  1209,   271,
           441,   272,  3787,  8863,    25,  4610,    39, 13359, 48190]],
       device='cuda:0'), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]],
       device='cuda:0'), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]],
       device='cuda:0')}

In [11]:
with torch.cuda.amp.autocast():
    output_tokens = model.generate(
        input_ids = batch.input_ids, 
        max_new_tokens=300,
        temperature=0.7,
        top_p=0.7,
        num_return_sequences=1,
        pad_token_id=tokenizer.eos_token_id,
        eos_token_id=tokenizer.eos_token_id,
    )

In [12]:
generated_text = tokenizer.decode(output_tokens[0], skip_special_tokens=True)
# Inspect message response in the outputs
print(generated_text.split("<human>: ")[1].split("<bot>: ")[-1])

Here are four things to do in San Francisco:

1. Visit the Golden Gate Bridge: The Golden Gate Bridge is one of the most iconic landmarks in San Francisco and a must-see for any visitor. You can walk or bike across the bridge, or take a ferry to get a closer look.

2. Explore the Fisherman's Wharf: The Fisherman's Wharf is a popular tourist destination with a variety of restaurants, shops, and attractions. You can try some fresh seafood, take a boat tour, or visit the Aquarium of the Bay.

3. Visit the Alcatraz Island: Alcatraz Island is a former federal prison that is now a national park and a popular tourist destination. You can take a ferry to the island and explore the prison, learn about its history, and enjoy the beautiful views of the city.

4. Take a cable car ride: San Francisco's cable cars are a unique and fun way to get around the city. You can ride the cable cars up and down the city's steep hills and enjoy the views along the way.

These are just a few of the many things 